In [ ]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import json
import numpy as np
import scipy as sp
import scipy.stats as st
import scipy.integrate as integrate
from sklearn import linear_model
import matplotlib.patches as mpatches

sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
sns_colors = sns.color_palette()
figsize = (15,8)
legend_fontsize = 16

from matplotlib import rc
rc('font',**{'family':'sans-serif'})
rc('text', usetex=True)
rc('text.latex',preamble=r'\usepackage[utf8]{inputenc}')
rc('text.latex',preamble=r'\usepackage[russian]{babel}')
rc('figure', **{'dpi': 300})

## Выбор модели в полиномиальной регрессии

In [ ]:
## Оверфиттинг
## Исходная функция
orig = lambda x : np.sin(2*x)

## X-координаты точек данных
xd = np.arange(-1.5, 2, 7/60)
# xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
# xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
num_points = len(xd)

## Данные
data = orig(xd) + np.random.normal(0, .25, num_points)

## Для рисования
xs = np.arange(xd[0]-1.5, xd[-1]+1.5, 0.01)

## Обучаем модель с регуляризацией
def train_model(xs, ys, alpha=0, use_lasso=False):
    if alpha == 0:
        return linear_model.LinearRegression(fit_intercept=True).fit( xs, ys )
    else:
        if use_lasso:
            return linear_model.Lasso(alpha=alpha, fit_intercept=True).fit( xs, ys )
        else:
            return linear_model.Ridge(alpha=alpha, fit_intercept=True).fit( xs, ys )

In [ ]:
## Выделение полиномиальных признаков
xs_d = np.vstack([xs ** i for i in range(1, num_points+1)]).transpose()
xd_d = np.vstack([xd ** i for i in range(1, num_points+1)]).transpose()

## Какие степени многочлена будем обучать и рисовать
set_of_powers = [ 1, 3, 7 ]

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-2, 2))
ax.scatter(xd, data, marker='*', s=120)
ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")

for d in set_of_powers:
    if d == 0:
        print(np.mean(data))
        ax.hlines(np.mean(data), xmin=xs[0], xmax=xs[-1], label="$d=0$", linestyle="dashed")
    else:
        cur_model = train_model( xd_d[:, :d], data, alpha=0.1 )
        print(cur_model.coef_)
        ax.plot(xs, cur_model.predict( xs_d[:, :d] ), linewidth=2, label="$d=%d$" % d)

ax.legend(loc="lower center", fontsize=legend_fontsize)
# fig.savefig(output_directory + 'ms1.pdf', bbox_inches='tight')

In [ ]:
def get_X(d):
    return np.hstack([np.ones(xd_d[:, :d].shape[0]).reshape(-1, 1), xd_d[:, :d]])

In [ ]:
def linregr_sigma(X, y):
    N = X.shape[0]
    XtX = X.T.dot(X)
    mu = np.linalg.inv(XtX).dot(X.T).dot(data)
    preds = X.dot(mu)
    sigma2 = (np.sum((preds-data)**2) / N)
    return mu, sigma2

In [ ]:
N, dmax = data.shape[0], 12
lrs = [ linregr_sigma( get_X(d), data ) for d in range(1, dmax) ]

In [ ]:
def logL(lr, N, d):
    return -.5*N*(np.log(2*np.pi) + np.log(lr[1])+1)

def BIC(lr, N, d):
    return N*(np.log(2*np.pi) + np.log(lr[1]) + 1) + np.log(N)*(d+2)

def AIC(lr, N, d):
    return N*(np.log(2*np.pi) + np.log(lr[1]) + 1) + 2*(d+2)

In [ ]:
ds = np.arange(1, dmax)
logLs = [logL(lrs[d-1], N, d) for d in ds]
AICs = [AIC(lrs[d-1], N, d) for d in ds]
BICs = [BIC(lrs[d-1], N, d) for d in ds]

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((1, dmax-2))
ax.plot(ds, logLs, label='Логарифм правдоподобия', linewidth=2, marker='.', markersize=10)
ax.plot(ds, AICs, label="AIC", linewidth=2, marker='.', markersize=10)
ax.plot(ds, BICs, label="BIC", linewidth=2, marker='.', markersize=10)
ax.legend(fontsize=legend_fontsize)

## AIC

In [ ]:
true_w, sigma = -.5, .5
orig = lambda x : true_w*x
xd = np.array([-3, -1, 0, 0.5, 2.5]) / 2
num_points = len(xd)

## Данные
# data = orig(xd) + np.random.normal(0, sigma, num_points)
data = np.array([ 0.66,  0.38, -0.27, -0.21,  0.23])
# data = np.array([ 1.18, -0.08, -0.31, 0.26, 0.72])
m = linear_model.LinearRegression(fit_intercept=False).fit( xd.reshape(-1, 1), data)
print(m.coef_)

## Для рисования
def plot_linear_graph(xd, data, m, fname=None):
    xs = np.arange(xd[0]-1.5, xd[-1]+1.5, 0.01)
    fig = plt.figure(figsize=(5,6))
    ax = fig.add_subplot(111)
    ax.set_xlim((xs[0], xs[-1]))
    ax.set_ylim((-2.5, 2.5))
    ax.scatter(xd, data, marker='*', s=120)
    ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")
    ax.plot(xs, m.predict(xs.reshape(-1, 1)), linewidth=2, label="Линейная регрессия")
    ax.legend(loc="lower left", fontsize=legend_fontsize)
    if fname is not None:
        fig.savefig(output_directory + fname + '.pdf', bbox_inches='tight')

plot_linear_graph(xd, data, m)

In [ ]:
def log_likelihood(w, xd=xd, data=data, sigma=sigma):
    return - np.sum((data - w*xd)**2) / (2 * (sigma**2))

def expected_log_l(w, xd=xd, data=data, sigma=sigma):
#     return - np.sum(orig(xd) ** 2 + (sigma**2) - 2*orig(xd)*(w*xd) + (w*xd) **2) / (2 * (sigma**2))
    return - len(data) / 2. - np.sum(((w-true_w)*xd) ** 2) / (2 * (sigma**2))

In [ ]:
def text_between(ax, x, y1, y2, text, rotation=0):
    ax.text(x, (y1+y2)/2, text, horizontalalignment='left', verticalalignment='center', rotation=rotation)

def plot_nice_graph(true_w=true_w, m=m, data=data, fname=None, xlim=(-1, 0.55), ylim=(-3.5, -0.4), B2x=.35):
    fig = plt.figure(figsize=(9,6))
    ax = fig.add_subplot(111)
    xxs = np.arange(xlim[0], xlim[1], 0.01)
    ax.set_xlim((xxs[0], xxs[-1]))
    ax.set_ylim(ylim)
    print(data)
    print(m.coef_)
    ax.plot(xxs, np.vectorize(lambda x: log_likelihood(x, data=data))(xxs), linewidth=2, label="$\log p(\mathbf{y}|\mathbf{w},X)$", color=palette[0])
    ax.plot(xxs, np.vectorize(lambda x: expected_log_l(x, data=data))(xxs), linewidth=2, label=r'$\mathrm{E}_{\mathbf{y}\sim p_{\mathrm{data}}}\left[\log p(\mathbf{y}|\mathbf{w},X)\right]$', color=palette[1])
    
    logl_w0, logl_w = log_likelihood(true_w, data=data), log_likelihood(m.coef_[0], data=data)
    expl_w0, expl_w = expected_log_l(true_w, data=data), expected_log_l(m.coef_[0], data=data)
    
    B1 = logl_w - logl_w0
    B2 = logl_w0 - expl_w0
    B3 = expl_w0 - expl_w
    print(B1, B2, B3)
    
    ax.scatter(true_w, expl_w0, marker='o', s=20, zorder=10, color="black")
    ax.scatter(true_w, logl_w0, marker='o', s=20, zorder=10, color="black")
    ax.scatter(m.coef_[0], logl_w, marker='o', s=20, zorder=10, color="black")
    ax.scatter(m.coef_[0], expl_w, marker='o', s=20, zorder=10, color="black")

    ax.vlines(m.coef_[0], ylim[0], max(expl_w, logl_w), color="black", linestyle='--', linewidth=1)
    ax.vlines(true_w, ylim[0], max(expl_w0, logl_w0), color="black", linestyle='--', linewidth=1)
    ax.set_xticks([-1, -.8, 0, 0.2, 0.4])
    ax.set_yticks([ylim[1]-.1, logl_w, logl_w0, expl_w0, expl_w])
    ax.set_yticklabels([r'$%.2f$' % (ylim[1]-.1), r'$\log p(\mathbf{y}|{w}_{\mathrm{ML}})=%.2f$' % logl_w, r'$\log p(\mathbf{y}|{w}_{\mathrm{true}})=%.2f$' % logl_w0, r'$\mathrm{E}\left[\log p(\mathbf{y}|w_{\mathrm{true}})\right]=%.2f$' % expl_w0, r'$\mathrm{E}\left[\log p(\mathbf{y}|{w}_{\mathrm{ML}})\right]=%.2f$' % expl_w])
    ax.text(true_w, ylim[0]-.1, r'$w_{\mathrm{true}}=%.1f$' % true_w, horizontalalignment='center')
    ax.text(m.coef_[0], ylim[0]-.1, r'$w_{\mathrm{ML}}=%.2f$' % m.coef_[0], horizontalalignment='center')
    ax.hlines(logl_w, .52, m.coef_[0], color="black", linestyle='-', linewidth=.8)
    ax.hlines( expl_w, .52, m.coef_[0], color="black", linestyle='-', linewidth=.8)
    ax.hlines(logl_w0, .38, true_w, color="black", linestyle='-', linewidth=.8)
    ax.hlines(np.vectorize(lambda x: expected_log_l(x, data=data))(true_w), .38, true_w, color="black", linestyle='-', linewidth=.8)
    # ax.text(.44, (expected_log_l_vec(m.coef_[0])+log_likelihood(m.coef_[0]))/2, r'$b(p_{\mathrm{data}})$', horizontalalignment='left', verticalalignment='center', rotation=90)
    p1 = mpatches.FancyArrowPatch((.5,expl_w), (.5, logl_w), mutation_scale=10, arrowstyle='<->', color="black", shrinkA=0, shrinkB=0)
    ax.add_patch(p1)
    p2 = mpatches.FancyArrowPatch((.35, expl_w), (.35, expl_w0), mutation_scale=10, arrowstyle='<->', color="black", shrinkA=0, shrinkB=0)
    ax.add_patch(p2)
    p3 = mpatches.FancyArrowPatch((B2x, logl_w0), (B2x, expl_w0), mutation_scale=10, arrowstyle='<->', color="black", shrinkA=0, shrinkB=0)
    ax.add_patch(p3)
    p4 = mpatches.FancyArrowPatch((.35, logl_w0), (.35, logl_w), mutation_scale=10, arrowstyle='<->', color="black", shrinkA=0, shrinkB=0)
    ax.add_patch(p4)

    text_between(ax, .44, expl_w, logl_w, r'$b(p_{\mathrm{data}})$', rotation=90)
    text_between(ax, .28, expl_w, expl_w0, r'$B_3$')
    text_between(ax, B2x-.07, expl_w0, logl_w0, r'$B_2$')
    text_between(ax, .28, logl_w0, logl_w, r'$B_1$')

    ax.legend(fontsize=legend_fontsize)
    
plot_nice_graph(true_w, m, data)

In [ ]:
data = np.array([ 1.18, -0.08, -0.31, 0.26, 0.72])
m = linear_model.LinearRegression(fit_intercept=False).fit( xd.reshape(-1, 1), data)
print(m.coef_)
plot_linear_graph(xd, data, m)
plot_nice_graph(true_w, m, data, ylim=(-5.1, -1.8), B2x=.2)

In [ ]:
def get_B(data, xd=xd):
    m = linear_model.LinearRegression(fit_intercept=False).fit( xd.reshape(-1, 1), data)
    logl_w0, logl_w = log_likelihood(true_w, data=data), log_likelihood(m.coef_[0], data=data)
    expl_w0, expl_w = expected_log_l(true_w, data=data), expected_log_l(m.coef_[0], data=data)
    B1 = logl_w - logl_w0
    B2 = logl_w0 - expl_w0
    B3 = expl_w0 - expl_w
    return [B1, B2, B3]

B = np.vstack([ get_B(orig(xd) + np.random.normal(0, sigma, num_points)) for _ in range(1000) ])
print("B1 = %.3f +- %.3f" % (np.mean(B[:,0]), np.std(B[:,0])))
print("B2 = %.3f +- %.3f" % (np.mean(B[:,1]), np.std(B[:,1])))
print("B3 = %.3f +- %.3f" % (np.mean(B[:,2]), np.std(B[:,2])))

In [ ]:
def plot_simple_hist(data):
    fig = plt.figure(figsize=(4,4))
    ax = fig.add_subplot(111)
    ax.set_xlim((np.min(data), np.max(data)))
    sns.histplot(data, ax=ax, kde=True, stat='probability')
    ax.set_ylabel(None)

plot_simple_hist(B[:,0])
plot_simple_hist(B[:,1])
plot_simple_hist(B[:,2])